In [1]:
import warnings
from collections import namedtuple
from pathlib import Path

import autokeras as ak
import keras.backend as K
import numpy as np
import pandas as pd
from keras.models import load_model
from keras_tuner.engine import hyperparameters
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import train_test_split

warnings.filterwarnings("ignore")

Using TensorFlow backend


Loading datasets

In [2]:
base_path = Path('dataset/dataset_versions')

datasets = {}
datasets_names = (
    'bfill_ffill',
    'linear_interpolation',
    'cubic_interpolation',
    'quadratic_interpolation',
    'polynomial_5_interpolation',
    'polynomial_7_interpolation',
    'polynomial_9_interpolation',
    'polynomial_11_interpolation',
)
for dataset_name in datasets_names:
    dataset = pd.read_excel(base_path / f'{dataset_name}_rescaled_dataset.xlsx')
    datasets[dataset_name] = dataset.iloc[:, 1:]

Split datasets

In [3]:
test_size = 0.2
seed = 7
target_feature_name = 'GDP per capita (current US$)'

SplittedDataset = namedtuple('SplittedDataset', ['name', 'x_train', 'y_train', 'x_test', 'y_test'])
splited_datasets = []

for dataset_name, dataset in datasets.items():
    model = dict()
    model['name'] = dataset_name
    data_x = dataset.drop([target_feature_name], axis=1)
    data_y = dataset[target_feature_name]
    model['x_train'], model['x_test'], model['y_train'], model['y_test'] = train_test_split(data_x, data_y, test_size=test_size, random_state=seed)
    splited_datasets.append(SplittedDataset(model['name'], model['x_train'],  model['y_train'], model['x_test'], model['y_test']))

Define custom metrics and custom loss functions for training models

In [4]:
def r2_score_custom(y_true, y_pred):
    SS_res =  K.sum(K.square(y_true - y_pred))
    SS_tot = K.sum(K.square(y_true - K.mean(y_true)))
    r2 = 1 - SS_res/(SS_tot + K.epsilon())
    return r2

def r2_loss(y_true, y_pred):
    return -r2_score_custom(y_true, y_pred)

Try to get the best model on each dataset

In [4]:
for dataset in splited_datasets:
    clf = ak.StructuredDataRegressor(
        max_trials=500,
        project_name=f'models_for_{dataset.name}',
        loss=r2_loss,
        metrics=[r2_score_custom])
    clf.fit(dataset.x_train, dataset.y_train)

Trial 115 Complete [00h 02m 40s]
val_loss: 18.074037551879883

Best val_loss So Far: -1.7762184143066406e-05
Total elapsed time: 01h 34m 23s
Epoch 1/19
7/7 [==============================] - 7s 12ms/step - loss: 22871.3281 - r2_score_custom: -34992.4570
Epoch 2/19
7/7 [==============================] - 0s 13ms/step - loss: 2506.4795 - r2_score_custom: -4351.9873
Epoch 3/19
7/7 [==============================] - 0s 11ms/step - loss: 1165.3774 - r2_score_custom: -2229.0417
Epoch 4/19
7/7 [==============================] - 0s 12ms/step - loss: 440.4140 - r2_score_custom: -813.8995
Epoch 5/19
7/7 [==============================] - 0s 12ms/step - loss: 30.1362 - r2_score_custom: -38.9049
Epoch 6/19
7/7 [==============================] - 0s 12ms/step - loss: 55.3398 - r2_score_custom: -118.9700
Epoch 7/19
7/7 [==============================] - 0s 13ms/step - loss: 49.3822 - r2_score_custom: -93.2930
Epoch 8/19
7/7 [==============================] - 0s 11ms/step - loss: 3.9268 - r2_score_cust

Train each model on each data set to find the best model

In [23]:
result = []
for model_name in splited_datasets:
    model = load_model(f'models_for_{model_name.name}/best_model', custom_objects={"r2_loss": r2_loss, "r2_score_custom": r2_score_custom})
    for dataset in splited_datasets:
        model.fit(dataset.x_train, dataset.y_train, epochs=1000)
        test_predict = model.predict(dataset.x_test)
        rmse = np.sqrt(mean_squared_error(dataset.y_test, test_predict))
        r2 = r2_score(dataset.y_test, test_predict)
        result.append({
            'dataset_name': dataset.name,
            'model_for_dataset': model_name.name,
            'r2': r2,
            'rmse': rmse
        })

Epoch 1/1000
7/7 [==============================] - 8s 22ms/step - loss: 0.3469 - r2_score_custom: -0.3369
Epoch 2/1000
7/7 [==============================] - 0s 23ms/step - loss: -0.4044 - r2_score_custom: 0.4032
Epoch 3/1000
7/7 [==============================] - 0s 23ms/step - loss: -0.7869 - r2_score_custom: 0.7899
Epoch 4/1000
7/7 [==============================] - 0s 22ms/step - loss: -0.8982 - r2_score_custom: 0.8958
Epoch 5/1000
7/7 [==============================] - 0s 23ms/step - loss: -0.9207 - r2_score_custom: 0.9103
Epoch 6/1000
7/7 [==============================] - 0s 24ms/step - loss: -0.9404 - r2_score_custom: 0.9397
Epoch 7/1000
7/7 [==============================] - 0s 44ms/step - loss: -0.9434 - r2_score_custom: 0.9360
Epoch 8/1000
7/7 [==============================] - 0s 21ms/step - loss: -0.9545 - r2_score_custom: 0.9554
Epoch 9/1000
7/7 [==============================] - 0s 20ms/step - loss: -0.9544 - r2_score_custom: 0.9533
Epoch 10/1000
7/7 [==================

Display the results

In [24]:
print(f'{"dataset_name".center(30)} | {"model_for_dataset".center(30)} |{"r^2".center(20)} | {"rmse".center(20)}')
for row in result:
    print(f'{str(row["dataset_name"]).ljust(30)} | {str(row["model_for_dataset"]).ljust(30)} |{str(row["r2"]).center(20)} | {str(row["rmse"]).center(20)}')

         dataset_name          |       model_for_dataset        |        r^2          |         rmse        
bfill_ffill                    | bfill_ffill                    | 0.983197706167756   | 0.021048333170706396
linear_interpolation           | bfill_ffill                    | 0.9813126488786346  | 0.022031695600975888
cubic_interpolation            | bfill_ffill                    | 0.9836733848260262  | 0.02082292924826878 
quadratic_interpolation        | bfill_ffill                    | 0.9820418111356801  | 0.021871507245492992
polynomial_5_interpolation     | bfill_ffill                    | 0.9702946306219572  | 0.02874867891876567 
polynomial_7_interpolation     | bfill_ffill                    | 0.9609575748957818  | 0.019151272312399284
polynomial_9_interpolation     | bfill_ffill                    | 0.9191083922816975  | 0.016459322588328072
polynomial_11_interpolation    | bfill_ffill                    | 0.9204863128545612  | 0.016974365430327928

bfill_ffill       

In [4]:
bfill_ffill = [0.983197706167756, 0.9813126488786346, 0.9836733848260262, 0.9820418111356801, 0.9702946306219572, 0.9609575748957818, 0.9191083922816975, 0.9204863128545612]
linear_interpolation = [0.9886995165684891, 0.9912607418826018, 0.9922551272333145, 0.9928277727132357, 0.9926015407441224, 0.98560976727146,0.9187040636917752, -0.057858903531160966]
cubic_interpolation = [0.9905765056778177,0.9939117934993655, 0.9953976497729077, 0.9942679473627865, 0.9934861113158872, 0.9895511661344554,  0.9878744371650884, 0.9927168796791049]
quadratic_interpolation = [0.9904276332402913, 0.9939664547500987, 0.9937762506716373, 0.9940868137280644, 0.9936528236935309,0.9769505237128211, 0.9812681679078445, 0.9262636500068495]
polynomial_5_interpolation = [0.9892910001435251, 0.9943347094204255, 0.9830867082769769, 0.9893225747751156 , 0.9940267632803975, 0.9674025347077245, 0.9161757903399134, 0.9571140962298677]
polynomial_7_interpolation = [0.971759087802232, 0.9715440973870297, 0.9570119031006681, 0.9846024692831911, 0.9630345940336447,  0.9813011292321029, 0.9800242852409466,  0.988853615493004 ]
polynomial_9_interpolation = [-0.17288247245777022, -0.1967844234504208, -0.17579649424799015, -0.1259291732550316, -0.1435494524735672, -0.051362019237973344, -0.06154435746628528, -0.03368472817818069]
polynomial_11_interpolation = [-0.12970280099571174, -0.00026828913286713885, -0.21717367477494354, -0.1607049545577932, -0.1503092233446286, -0.07304546793039002,  -0.09662140371392636, -0.07581980532771992]
r2_list = [bfill_ffill, linear_interpolation, cubic_interpolation, quadratic_interpolation, polynomial_5_interpolation, polynomial_7_interpolation, polynomial_9_interpolation, polynomial_11_interpolation]

Look at the average value of the coefficient of determination for the models

In [5]:
for r2_for_model in r2_list:
    print(sum(r2_for_model)/len(r2_for_model))

0.9626340577077619
0.8505124533217296
0.9922228113259267
0.9812990397138922
0.9738442721467432
0.9747663976966023
-0.12019164009590241
-0.11295570247224757


See the smallest and largest value for the coefficient of determination

In [6]:
for r2_for_model in r2_list:
    print(max(r2_for_model), min(r2_for_model))

0.9836733848260262 0.9191083922816975
0.9928277727132357 -0.057858903531160966
0.9953976497729077 0.9878744371650884
0.9940868137280644 0.9262636500068495
0.9943347094204255 0.9161757903399134
0.988853615493004 0.9570119031006681
-0.03368472817818069 -0.1967844234504208
-0.00026828913286713885 -0.21717367477494354


Collecting the best datasets

In [5]:
bfill_ffill_dataset = splited_datasets[0]
cubic_interpolation_dataset = splited_datasets[2]
quadratic_interpolation_dataset = splited_datasets[3]
best_datasets = [bfill_ffill_dataset, cubic_interpolation_dataset, quadratic_interpolation_dataset]

Let's take a closer look at the resulting models

In [34]:
bfill_ffill_model = load_model(f'automl/models_for_{bfill_ffill_dataset.name}/best_model', custom_objects={"r2_loss": r2_loss, "r2_score_custom": r2_score_custom})
bfill_ffill_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223)]            0         
                                                                 
 multi_category_encoding (Mu  (None, 1223)             0         
 ltiCategoryEncoding)                                            
                                                                 
 dense (Dense)               (None, 64)                78336     
                                                                 
 re_lu (ReLU)                (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 1024)              66560     
                                                                 
 re_lu_1 (ReLU)              (None, 1024)              0         
                                                             

In [35]:
for layer in bfill_ffill_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'multi_category_encoding', 'trainable': True, 'dtype': 'float32', 'encoding': ListWrapper(['none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none'

In [36]:
cubic_interpolation_model = load_model(f'automl/models_for_{cubic_interpolation_dataset.name}/best_model', custom_objects={"r2_loss": r2_loss, "r2_score_custom": r2_score_custom})
cubic_interpolation_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223)]            0         
                                                                 
 multi_category_encoding (Mu  (None, 1223)             0         
 ltiCategoryEncoding)                                            
                                                                 
 dense (Dense)               (None, 512)               626688    
                                                                 
 re_lu (ReLU)                (None, 512)               0         
                                                                 
 dense_1 (Dense)             (None, 32)                16416     
                                                                 
 re_lu_1 (ReLU)              (None, 32)                0         
                                                             

In [37]:
for layer in cubic_interpolation_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'multi_category_encoding', 'trainable': True, 'dtype': 'float32', 'encoding': ListWrapper(['none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none'

In [38]:
quadratic_interpolation_model = load_model(f'automl/models_for_{quadratic_interpolation_dataset.name}/best_model', custom_objects={"r2_loss": r2_loss, "r2_score_custom": r2_score_custom})
quadratic_interpolation_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223)]            0         
                                                                 
 multi_category_encoding (Mu  (None, 1223)             0         
 ltiCategoryEncoding)                                            
                                                                 
 dense (Dense)               (None, 256)               313344    
                                                                 
 re_lu (ReLU)                (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 32)                8224      
                                                                 
 re_lu_1 (ReLU)              (None, 32)                0         
                                                             

In [39]:
for layer in quadratic_interpolation_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'multi_category_encoding', 'trainable': True, 'dtype': 'float32', 'encoding': ListWrapper(['none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none', 'none'

Trying to get models with LSTM and GRU in the composition

In [10]:
for dataset in best_datasets:
    for layer_type in ['gru', 'lstm']:
        input_node = ak.Input()
        output_node = ak.RNNBlock(layer_type=layer_type)(input_node)
        output_node = ak.DenseBlock(hyperparameters.Choice("num_layers", [6,7,8]))(output_node)
        output_node = ak.RegressionHead()(output_node)
        auto_model = ak.AutoModel(
            inputs=input_node,
            outputs=output_node,
            max_trials=500,
            overwrite=True,
            project_name=f'nm_for_{dataset.name}_{layer_type}',
        )
        x = dataset.x_train.to_numpy().reshape(203, 1223, 1)
        y = dataset.y_train.to_numpy().reshape(203, 1, 1)
        auto_model.fit(x, y, epochs=100)


Trial 157 Complete [00h 01m 10s]
val_loss: 0.0612630620598793

Best val_loss So Far: 0.0019144024699926376
Total elapsed time: 11h 54m 30s
Epoch 1/100
7/7 [==============================] - 9s 604ms/step - loss: 0.0835 - mean_squared_error: 0.0835
Epoch 2/100
7/7 [==============================] - 5s 648ms/step - loss: 0.0598 - mean_squared_error: 0.0598
Epoch 3/100
7/7 [==============================] - 5s 647ms/step - loss: 0.0524 - mean_squared_error: 0.0524
Epoch 4/100
7/7 [==============================] - 5s 655ms/step - loss: 0.0531 - mean_squared_error: 0.0531
Epoch 5/100
7/7 [==============================] - 5s 659ms/step - loss: 0.0524 - mean_squared_error: 0.0524
Epoch 6/100
7/7 [==============================] - 5s 658ms/step - loss: 0.0521 - mean_squared_error: 0.0521
Epoch 7/100
7/7 [==============================] - 5s 664ms/step - loss: 0.0518 - mean_squared_error: 0.0518
Epoch 8/100
7/7 [==============================] - 5s 667ms/step - loss: 0.0519 - mean_squared_err

INFO:tensorflow:Assets written to: .\nm_for_quadratic_interpolation_lstm\best_model\assets


INFO:tensorflow:Assets written to: .\nm_for_quadratic_interpolation_lstm\best_model\assets


Let's take a closer look at the resulting models

In [26]:
bfill_ffill_gru_model = load_model(f'automl/nm_for_bfill_ffill_gru_v1/best_model')
bfill_ffill_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 1223, 2)          30        
 nal)                                                            
                                                                 
 bidirectional_2 (Bidirectio  (None, 2)                30        
 nal)                                                        

In [27]:
for layer in bfill_ffill_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [28]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 170ms/step
0.8817273629792818 0.05584387700546064


In [29]:
bfill_ffill_lstm_model = load_model(f'automl/nm_for_bfill_ffill_lstm_v1/best_model')
bfill_ffill_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                32        
 nal)                                                            
                                                                 
 regression_head_1 (Dense)   (None, 1)                 3         
                                                             

In [30]:
for layer in bfill_ffill_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_co

In [31]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 112ms/step
0.5508578178732593 0.10882416517411109


In [32]:
quadratic_interpolation_gru_model = load_model('automl/nm_for_quadratic_interpolation_gru_v1/best_model')
quadratic_interpolation_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 1223, 2)          30        
 nal)                                                            
                                                                 
 bidirectional_2 (Bidirectio  (None, 2)                30        
 nal)                                                        

In [33]:
for layer in quadratic_interpolation_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [34]:
x = quadratic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = quadratic_interpolation_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(quadratic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(quadratic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 170ms/step
0.8350382634733073 0.06628863182342841


In [35]:
quadratic_interpolation_lstm_model = load_model('automl/nm_for_quadratic_interpolation_lstm_v1/best_model')
quadratic_interpolation_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                32        
 nal)                                                            
                                                                 
 regression_head_1 (Dense)   (None, 1)                 3         
                                                             

In [36]:
for layer in quadratic_interpolation_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_co

In [37]:
x = quadratic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = quadratic_interpolation_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(quadratic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(quadratic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 104ms/step
0.7567249398008417 0.08050006664205342


In [38]:
cubic_interpolation_gru_model = load_model('automl/nm_for_cubic_interpolation_gru_v1/best_model')
cubic_interpolation_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 1223, 2)          30        
 nal)                                                            
                                                                 
 bidirectional_2 (Bidirectio  (None, 2)                30        
 nal)                                                        

In [39]:
for layer in cubic_interpolation_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [40]:
x = cubic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = cubic_interpolation_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(cubic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(cubic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 3s 341ms/step
0.8417337893971787 0.06483176533280827


In [41]:
cubic_interpolation_lstm_model = load_model('automl/nm_for_cubic_interpolation_lstm_v1/best_model')
cubic_interpolation_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 1223, 2)          32        
 nal)                                                            
                                                                 
 bidirectional_2 (Bidirectio  (None, 2)                32        
 nal)                                                        

In [42]:
for layer in cubic_interpolation_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_co

In [43]:
x = cubic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = cubic_interpolation_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(cubic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(cubic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 3s 224ms/step
0.6649577348439698 0.09432863358048121


In [44]:
bfill_ffill_gru_model = load_model(f'automl/nm_for_bfill_ffill_gru_v2/best_model')
bfill_ffill_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                30        
 nal)                                                            
                                                                 
 dense (Dense)               (None, 32)                96        
                                                             

In [45]:
for layer in bfill_ffill_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [46]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 254ms/step
0.909118535973618 0.04895207202442275


In [47]:
bfill_ffill_lstm_model = load_model(f'automl/nm_for_bfill_ffill_lstm_v2/best_model')
bfill_ffill_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                32        
 nal)                                                            
                                                                 
 dense (Dense)               (None, 512)               1536      
                                                             

In [48]:
for layer in bfill_ffill_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_co

In [49]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 118ms/step
0.9049019040460151 0.0500748126051227


In [50]:
quadratic_interpolation_gru_model = load_model('automl/nm_for_quadratic_interpolation_gru_v2/best_model')
quadratic_interpolation_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                30        
 nal)                                                            
                                                                 
 dense (Dense)               (None, 32)                96        
                                                             

In [51]:
for layer in quadratic_interpolation_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [52]:
x = quadratic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = quadratic_interpolation_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(quadratic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(quadratic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 250ms/step
0.8061846022392328 0.07185245046630635


In [53]:
quadratic_interpolation_lstm_model = load_model('automl/nm_for_quadratic_interpolation_lstm_v2/best_model')
quadratic_interpolation_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                32        
 nal)                                                            
                                                                 
 dense (Dense)               (None, 32)                96        
                                                             

In [54]:
for layer in quadratic_interpolation_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_co

In [55]:
x = quadratic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = quadratic_interpolation_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(quadratic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(quadratic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 125ms/step
0.8801449654216826 0.056503530722208276


In [56]:
cubic_interpolation_gru_model = load_model('automl/nm_for_cubic_interpolation_gru_v2/best_model')
cubic_interpolation_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 1223, 2)          24        
 l)                                                              
                                                                 
 bidirectional_1 (Bidirectio  (None, 2)                30        
 nal)                                                            
                                                                 
 dense (Dense)               (None, 32)                96        
                                                             

In [57]:
for layer in cubic_interpolation_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'GRU', 'config': {'name': 'gru', 'trainable': True, 'dtype': 'float32', 'return_sequences': True, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_constraint': None, 'dropout': 

In [58]:
x = cubic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = cubic_interpolation_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(cubic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(cubic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 239ms/step
0.8433259331125202 0.06450484020748425


In [59]:
cubic_interpolation_lstm_model = load_model('automl/nm_for_cubic_interpolation_lstm_v2/best_model')
cubic_interpolation_lstm_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 bidirectional (Bidirectiona  (None, 2)                24        
 l)                                                              
                                                                 
 dense (Dense)               (None, 32)                96        
                                                                 
 re_lu (ReLU)                (None, 32)                0         
                                                                 
 dense_1 (Dense)             (None, 256)               8448  

In [60]:
for layer in cubic_interpolation_lstm_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'bidirectional', 'trainable': True, 'dtype': 'float32', 'layer': {'class_name': 'LSTM', 'config': {'name': 'lstm', 'trainable': True, 'dtype': 'float32', 'return_sequences': False, 'return_state': False, 'go_backwards': False, 'stateful': False, 'unroll': False, 'time_major': False, 'units': 1, 'activation': 'tanh', 'recurrent_activation': 'sigmoid', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'recurrent_initializer': {'class_name': 'Orthogonal', 'config': {'gain': 1.0, 'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'unit_forget_bias': True, 'kernel_regularizer': None, 'recurrent_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'recurrent_constraint': None, 'bias_c

In [61]:
x = cubic_interpolation_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = cubic_interpolation_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(cubic_interpolation_dataset.y_test, test_predict))
r2 = r2_score(cubic_interpolation_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 1s 44ms/step
0.715681168929398 0.08689535419349141


In [6]:
dataset = bfill_ffill_dataset
for layer_type in ['lstm']:
    input_node = ak.Input()
    output_node = ak.ConvBlock()(input_node)
    output_node = ak.RNNBlock(layer_type=layer_type)(output_node)
    output_node = ak.DenseBlock(hyperparameters.Choice("num_layers", [6,7,8]))(output_node)
    output_node = ak.RegressionHead()(output_node)
    auto_model = ak.AutoModel(
        inputs=input_node,
        outputs=output_node,
        max_trials=500,
        overwrite=True,
        project_name=f'nm_for_{dataset.name}_conv_{layer_type}',
    )
    x = dataset.x_train.to_numpy().reshape(203, 1223, 1)
    y = dataset.y_train.to_numpy().reshape(203, 1, 1)
    auto_model.fit(x, y, epochs=100)

Trial 223 Complete [00h 04m 37s]
val_loss: 0.0004738012212328613

Best val_loss So Far: 0.00010866070806514472
Total elapsed time: 17h 05m 50s

Search: Running Trial #224

Value             |Best Value So Far |Hyperparameter
3                 |3                 |conv_block_1/kernel_size
False             |False             |conv_block_1/separable
True              |True              |conv_block_1/max_pooling
3                 |2                 |conv_block_1/num_blocks
2                 |2                 |conv_block_1/num_layers
16                |16                |conv_block_1/filters_0_0
512               |512               |conv_block_1/filters_0_1
0.25              |0.25              |conv_block_1/dropout
32                |32                |conv_block_1/filters_1_0
32                |32                |conv_block_1/filters_1_1
True              |True              |rnn_block_1/bidirectional
2                 |2                 |rnn_block_1/num_layers
False             |False    

In [7]:
bfill_ffill_conv_gru_model = load_model('automl/nm_for_bfill_ffill_conv_gru/best_model')
bfill_ffill_conv_gru_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1223, 1)]         0         
                                                                 
 cast_to_float32 (CastToFloa  (None, 1223, 1)          0         
 t32)                                                            
                                                                 
 conv1d (Conv1D)             (None, 1221, 256)         1024      
                                                                 
 conv1d_1 (Conv1D)           (None, 1219, 32)          24608     
                                                                 
 max_pooling1d (MaxPooling1D  (None, 609, 32)          0         
 )                                                               
                                                                 
 conv1d_2 (Conv1D)           (None, 607, 512)          49664 

In [8]:
for layer in bfill_ffill_conv_gru_model.layers:
    print(layer.get_config())
    print()

{'batch_input_shape': (None, 1223, 1), 'dtype': 'float64', 'sparse': False, 'ragged': False, 'name': 'input_1'}

{'name': 'cast_to_float32', 'trainable': True, 'dtype': 'float32'}

{'name': 'conv1d', 'trainable': True, 'dtype': 'float32', 'filters': 256, 'kernel_size': (3,), 'strides': (1,), 'padding': 'valid', 'data_format': 'channels_last', 'dilation_rate': (1,), 'groups': 1, 'activation': 'relu', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'bias_constraint': None}

{'name': 'conv1d_1', 'trainable': True, 'dtype': 'float32', 'filters': 32, 'kernel_size': (3,), 'strides': (1,), 'padding': 'valid', 'data_format': 'channels_last', 'dilation_rate': (1,), 'groups': 1, 'activation': 'relu', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config

In [9]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_conv_gru_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 84ms/step
0.9971757684039496 0.00862945911744168


In [6]:
bfill_ffill_conv_lstm_model = load_model('automl/nm_for_bfill_ffill_conv_lstm/best_model')
bfill_ffill_conv_lstm_model.summary()

Model: "sequential_14"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_8 (Conv1D)           (None, 1221, 16)          64        
                                                                 
 conv1d_9 (Conv1D)           (None, 1219, 512)         25088     
                                                                 
 max_pooling1d_4 (MaxPooling  (None, 609, 512)         0         
 1D)                                                             
                                                                 
 dropout_18 (Dropout)        (None, 609, 512)          0         
                                                                 
 conv1d_10 (Conv1D)          (None, 607, 32)           49184     
                                                                 
 conv1d_11 (Conv1D)          (None, 605, 32)           3104      
                                                     

In [7]:
for layer in bfill_ffill_conv_lstm_model.layers:
    print(layer.get_config())
    print()

{'name': 'conv1d_8', 'trainable': True, 'dtype': 'float32', 'filters': 16, 'kernel_size': (3,), 'strides': (1,), 'padding': 'valid', 'data_format': 'channels_last', 'dilation_rate': (1,), 'groups': 1, 'activation': 'linear', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_constraint': None, 'bias_constraint': None}

{'name': 'conv1d_9', 'trainable': True, 'dtype': 'float32', 'filters': 512, 'kernel_size': (3,), 'strides': (1,), 'padding': 'valid', 'data_format': 'channels_last', 'dilation_rate': (1,), 'groups': 1, 'activation': 'linear', 'use_bias': True, 'kernel_initializer': {'class_name': 'GlorotUniform', 'config': {'seed': None}}, 'bias_initializer': {'class_name': 'Zeros', 'config': {}}, 'kernel_regularizer': None, 'bias_regularizer': None, 'activity_regularizer': None, 'kernel_cons

In [8]:
x = bfill_ffill_dataset.x_test.to_numpy().reshape(51, 1223, 1)
test_predict = bfill_ffill_conv_lstm_model.predict(x)
rmse = np.sqrt(mean_squared_error(bfill_ffill_dataset.y_test, test_predict))
r2 = r2_score(bfill_ffill_dataset.y_test, test_predict)
print(r2, rmse)

2/2 [==============================] - 2s 75ms/step
0.9847575712890481 0.020047513202124393
